# Week VI - Metropolis Algorithm

Today, we will focus on the **Metropolis algorithm**, which has been introduced to you in the lecture of yesterday. In particular, we will sample the distribution

$$P(x) = e^{\frac{-x^2}{2\sigma^2}}.$$

In order to do so, we will create a Python class that runs a Metropolis algorithm reproducing the distribution $P(x)$. We will employ a **Markov chain** obtained through **one random walker** behaving according to the following transition probability:

$$T(x_i \rightarrow x_j) = \min{\left[1,P(x_j)/P(x_i)\right]},$$

where the trial move is obtained with a uniformly distributed random variable $\tilde{x} \in [0,1) $

$$ x_j = x_i + \delta(\tilde{x}-0.5) $$

which is accepted if 

$$\tilde{x}_w \leq w = P(x_j)/P(x_i) = e^{\frac{-(x_j^2-x_i^2)}{2\sigma^2}} $$

with $\tilde{x}_w \in [0,1)$ also being a random variable following a uniform distribution.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

class Metropolis:
    '''
    This class implements 
    the Metropolis algorithm for a Gaussian distribution
    exp(-x**2/(2*sigma**2))
    '''
    
    def __init__(self,N,delta,sigma=1):
        'Initialise the Metropolis'
        self.N = N
        self.rng = np.random.default_rng(seed=42424)
        self.sigma = sigma
        self.delta = delta
        self.pref = -1.0/(2.0*self.sigma**2)
        self.acc = 0
        self.x = 0.0
        self.ar = None
        self.all_x = [self.x]
        self.all_x2 = None
        self.all_x3 = None
        self.all_x4 = None
        self.var = None
        self.counter = 0
        self.autocorr = []
        self.n_autocorr = 10
    
    def metro_step(self):
        'One step of Metropolis'
        rnd = self.rng.random()
        xp = self.x + self.delta * (rnd-0.5)
        p = self.x**2
        pp = xp**2
        w = np.exp(self.pref*(pp-p))
        rnd_w = self.rng.random()
        if (rnd_w<=w):
            self.x = xp 
            self.acc += 1
        self.all_x.append(self.x)
    
    def metro_driver(self):
        'Run N Metropolis steps.'
        for i in range(self.N):
            self.counter += 1
            self.metro_step()
    
    def get_hist(self):
        'Plot Histogram'
        plt.xlable('x')
        plt.ylable('count')
        plt.hist(self.all_x,bins=100)
        plt.show()
    
    @staticmethod
    def calc_autocorr(a,N):
        'Autocorrelation function'
        res = np.ones(N)
        for k in range(1,N):
            c_k = np.average(a[:-k]*a[k:]) 
            x_r = np.average(a[:-k])
            x_r_2 = np.average(a[:-k]**2)
            res[k] = (c_k-x_r**2)/(x_r_2-x_r**2)
        return res
    
    def get_stats(self):
        '''
        Calculate, store and print 
        statistical quantities
        '''
        self.ar = self.acc*1.0/self.N
        self.aver_x = np.average(self.all_x)
        self.aver_x2 = np.average(np.array(self.all_x)**2)
        self.aver_x3 = np.average(np.array(self.all_x)**3)
        self.aver_x4 = np.average(np.array(self.all_x)**4)
        self.var = self.aver_x2-self.aver_x**2
        print("Total number of steps run = {}".format(self.counter))
        print("Acceptance ratio = {}".format(self.ar))
        print("Sigma = {}, delta = {}".format(self.sigma,self.delta))
        print("<x> = {}, <x2> = {}".format(self.aver_x,self.aver_x2))
        print("<x3 = {}, <x4> = {}".format(self.aver_x3,self.aver_x4))
        print("variance = {}".format(self.var))
        
    def get_autocorr(self,n_autocorr=100):
        '''
        Wrapper for the autocorrelation
        function calculator
        '''
        a = np.array(self.all_x)
        self.autocorr = self.calc_autocorr(a,n_autocorr)

Let's run our first Metropolis!

In [ ]:
N= 100000
delta = 5
metro = Metropolis(N,delta)   #Comment to run multiple times
metro.metro_driver()
metro.get_stats()
metro.get_hist()

Let's study the effect of changing N. \
Also, how does the acceptance ratio change if we change $\sigma$?

In [ ]:
metro = Metropolis(10000,5)   
metro.metro_driver()
metro.get_stats()
metro.get_hist()

In [ ]:
x = np.arange(100,30000,100)
y = []
for N in x:
    metro = Metropolis(N,5)
    metro.metro_driver()
    metro.get_stats()
    y.append(1.0-metro.var)

In [ ]:
plt.xlabel('N')
plt.ylabel('$\sigma^2_{true}-\sigma^2_{calc}$')
plt.axhline(0.0,c='grey',alpha=0.5)
plt.axhline(0.05,ls='--',c='grey',alpha=0.5)
plt.axhline(-0.05,ls='--',c='grey',alpha=0.5)
plt.plot(x,y)
plt.show()

------------------------------------ 

## Autocorrelation function

Now let us investigate the autocorrelation function $c(k)$ for our Metropolis algorithm, which is defined as 

$$c(k) =\frac{<x_ix_{i+k}>-<x_i>^2}{<x_i^2>-<x_i>^2}.$$

In [ ]:
metro = Metropolis(10000,5) 
metro.metro_driver()
metro.get_stats()
metro.get_autocorr(n_autocorr=20) #try to increase it
plt.xlabel('k')
plt.ylabel('c(k)')
plt.plot(range(len(metro.autocorr)),metro.autocorr,'o-')
plt.axhline(0.0,c='grey',alpha=0.5)
plt.show()

- Now we study the autocorrelation as function of the integration step $\delta$.

In [ ]:
for delta in [1,5,10,25,50]:
    metro = Metropolis(10000,delta) 
    metro.metro_driver()
    metro.get_stats()
    metro.get_autocorr(n_autocorr=20)
    plt.xlabel('k')
    plt.ylabel('c(k)')
    xx = range(len(metro.autocorr))
    plt.plot(xx,metro.autocorr,'o-',label='$\delta =${}'.format(delta))
#plt.xlim([0,len(xx)])
plt.legend()
plt.show()

- Now let's try to calculate the same autocorrelation function for a normal distribution by using ad-hoc libraries for random number generators. Is it different with respect to our Metropolis algorithm?

In [ ]:
rng = np.random.default_rng(seed=42424)
N= 1000
a = rng.normal(size=N)
Nc = 10
c = Metropolis.calc_autocorr(a,Nc)
plt.xlabel('k')
plt.ylabel('c(k)')
plt.plot(range(Nc),c,'o-')
plt.axhline(0.0,c='grey',alpha=0.5)
plt.show()

In [ ]:
plt.hist(a)